# Tenant Vulnerability in LA

Hopefully this file will be helpful!

In [1]:
# import required packages
import pandas as pd
import geopandas as gpd
import numpy as np
import folium
import statistics
import matplotlib.pyplot as plt
import glob
import os

In [2]:
df_justice = gpd.read_file('data/LAJustice22Metrics.geojson')

ERROR 1: PROJ: proj_create_from_database: Open of /opt/conda/share/proj failed


In [3]:
df_justice.columns

Index(['FID', 'GEOID10', 'SF', 'CF', 'DF_PFS', 'AF_PFS', 'HDF_PFS', 'DSF_PFS',
       'EBF_PFS', 'EALR_PFS', 'EBLR_PFS', 'EPLR_PFS', 'HBF_PFS', 'LLEF_PFS',
       'LIF_PFS', 'LMI_PFS', 'PM25F_PFS', 'HSEF', 'P100_PFS', 'P200_I_PFS',
       'AJDLI_ET', 'LPF_PFS', 'KP_PFS', 'NPL_PFS', 'RMP_PFS', 'TSDF_PFS',
       'TPF', 'TF_PFS', 'UF_PFS', 'WF_PFS', 'UST_PFS', 'N_WTR', 'N_WKFC',
       'N_CLT', 'N_ENY', 'N_TRN', 'N_HSG', 'N_PLN', 'N_HLTH', 'SN_C', 'SN_T',
       'DLI', 'ALI', 'PLHSE', 'LMILHSE', 'ULHSE', 'EPL_ET', 'EAL_ET', 'EBL_ET',
       'EB_ET', 'PM25_ET', 'geometry'],
      dtype='object')

In [4]:
df_justice.head()

FID      GEOID10          SF                  CF  DF_PFS  AF_PFS  HDF_PFS  \
0  3595  06037482702  California  Los Angeles County    0.70    0.00     0.35   
1  3596  06037500201  California  Los Angeles County    0.30    0.01     0.33   
2  3597  06037500202  California  Los Angeles County    0.34    0.00     0.31   
3  3598  06037500300  California  Los Angeles County    0.42    0.00     0.13   
4  3599  06037500500  California  Los Angeles County    0.76    0.05     0.39   

   DSF_PFS  EBF_PFS  EALR_PFS  ...  ALI  PLHSE  LMILHSE  ULHSE  EPL_ET  \
0     0.91     0.08      0.00  ...    0      0        0      0       0   
1     0.80     0.06      0.12  ...    0      0        0      0       0   
2     0.81     0.06      0.10  ...    0      0        0      0       0   
3     0.87     0.06      0.20  ...    0      0        0      0       0   
4     0.88     0.27      0.00  ...    0      0        0      0       0   

   EAL_ET  EBL_ET  EB_ET  PM25_ET  \
0       0       0      0        1   
1       0       0      0        1   
2       0       0      0        1   
3       0       0      0        1   
4       0       0      0        1   

                                            geometry  
0  POLYGON ((-13150771.905 4034644.241, -13150748...  
1  POLYGON ((-13133894.979 4023954.365, -13133903...  
2  POLYGON ((-13133853.346 4024103.349, -13133877...  
3  POLYGON ((-13139892.874 4033202.951, -13139850...  
4  POLYGON ((-13145240.217 4031313.793, -13145175...  

[5 rows x 52 columns]

In [5]:
df_justice.crs

<Projected CRS: EPSG:3857>
Name: WGS 84 / Pseudo-Mercator
Axis Info [cartesian]:
- X[east]: Easting (metre)
- Y[north]: Northing (metre)
Area of Use:
- name: World between 85.06°S and 85.06°N.
- bounds: (-180.0, -85.06, 180.0, 85.06)
Coordinate Operation:
- name: Popular Visualisation Pseudo-Mercator
- method: Popular Visualisation Pseudo Mercator
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

In [6]:
df_justice = df_justice.to_crs(4326)
print(df_justice.crs)

EPSG:4326


In [7]:
# Grab average long and lat to center 
coords = df_justice.get_coordinates()
lon = []
lat = []
lon = coords['x']
lat = coords['y']
df_lon = lon[1].mean()
df_lat = lat[1].mean()
df_lat

33.95503061746988

In [8]:
neighborhoods = gpd.read_file('data/Census_Tract_Neighborhoods.csv')
neighborhoods.head()

GEOID                                              Tract  \
0  1400000US06037101110  Census Tract 1011.10, Los Angeles County, Cali...   
1  1400000US06037101122  Census Tract 1011.22, Los Angeles County, Cali...   
2  1400000US06037101210  Census Tract 1012.10, Los Angeles County, Cali...   
3  1400000US06037101220  Census Tract 1012.20, Los Angeles County, Cali...   
4  1400000US06037101300  Census Tract 1013, Los Angeles County, California   

  Tract Number Neighborhood                   Location    Latitude  \
0       101110      Tujunga  (34.2595555, -118.293602)  34.2595555   
1       101122      Tujunga    (34.267357, -118.29024)   34.267357   
2       101210      Tujunga  (34.251998, -118.2926875)   34.251998   
3       101220      Tujunga  (34.2511895, -118.281014)  34.2511895   
4       101300      Tujunga  (34.2455945, -118.271731)  34.2455945   

      Longitude geometry  
0   -118.293602     None  
1    -118.29024     None  
2  -118.2926875     None  
3   -118.281014     None  
4   -118.271731     None

In [9]:
neighborhoods.columns

Index(['GEOID', 'Tract', 'Tract Number', 'Neighborhood', 'Location',
       'Latitude', 'Longitude', 'geometry'],
      dtype='object')

In [10]:
neighborhoods['GEOID10'] = neighborhoods['GEOID'].str.slice(start=9)
neighborhoods.head()
neighborhoods = neighborhoods[[
    'GEOID10',
    'Neighborhood',
    'Location',
    'Latitude',
    'Longitude'
]]


In [11]:
neigh_geo = gpd.GeoDataFrame(
    neighborhoods, geometry=gpd.points_from_xy(neighborhoods['Longitude'], neighborhoods['Latitude']))

neigh_geo.head()

GEOID10 Neighborhood                   Location    Latitude  \
0  06037101110      Tujunga  (34.2595555, -118.293602)  34.2595555   
1  06037101122      Tujunga    (34.267357, -118.29024)   34.267357   
2  06037101210      Tujunga  (34.251998, -118.2926875)   34.251998   
3  06037101220      Tujunga  (34.2511895, -118.281014)  34.2511895   
4  06037101300      Tujunga  (34.2455945, -118.271731)  34.2455945   

      Longitude                     geometry  
0   -118.293602  POINT (-118.29360 34.25956)  
1    -118.29024  POINT (-118.29024 34.26736)  
2  -118.2926875  POINT (-118.29269 34.25200)  
3   -118.281014  POINT (-118.28101 34.25119)  
4   -118.271731  POINT (-118.27173 34.24559)

In [12]:
df_just_neigh = neigh_geo.merge(df_justice, on='GEOID10')
df_just_neigh

GEOID10                    Neighborhood  \
0     06037101110                         Tujunga   
1     06037101122                         Tujunga   
2     06037101210                         Tujunga   
3     06037101220                         Tujunga   
4     06037101300                         Tujunga   
...           ...                             ...   
2337  06037503801                       La Mirada   
2338  06037573902                      Long Beach   
2339  06037576602                      Long Beach   
2340  06037599100  Unincorporated Catalina Island   
2341  06037980033                       San Pedro   

                                  Location            Latitude  \
0                (34.2595555, -118.293602)          34.2595555   
1                  (34.267357, -118.29024)           34.267357   
2                (34.251998, -118.2926875)           34.251998   
3                (34.2511895, -118.281014)          34.2511895   
4                (34.2455945, -118.271731)          34.2455945   
...                                    ...                 ...   
2337       (33.899102856233, -117.9936485)  33.899102856232815   
2338       (33.8119735, -118.078652493167)  33.811973499999993   
2339  (33.765980150191, -118.170779302632)  33.765980150190742   
2340       (33.3888135, -118.423552636715)  33.388813499999998   
2341          (33.7513514674, -118.216154)  33.751351467400355   

                Longitude                   geometry_x    FID          SF  \
0             -118.293602  POINT (-118.29360 34.25956)   9681  California   
1              -118.29024  POINT (-118.29024 34.26736)  11577  California   
2            -118.2926875  POINT (-118.29269 34.25200)  10518  California   
3             -118.281014  POINT (-118.28101 34.25119)   6852  California   
4             -118.271731  POINT (-118.27173 34.24559)  11335  California   
...                   ...                          ...    ...         ...   
2337  -117.99364849999984  POINT (-117.99365 33.89910)   4913  California   
2338  -118.07865249316662  POINT (-118.07865 33.81197)   6335  California   
2339   -118.1707793026319  POINT (-118.17078 33.76598)   3915  California   
2340    -118.423552636715  POINT (-118.42355 33.38881)   7637  California   
2341  -118.21615399999982  POINT (-118.21615 33.75135)   8709  California   

                      CF  DF_PFS  ...  ALI  PLHSE  LMILHSE  ULHSE  EPL_ET  \
0     Los Angeles County    0.42  ...    0      0        0      0       0   
1     Los Angeles County    0.26  ...    0      0        0      0       0   
2     Los Angeles County    0.47  ...    0      0        0      0       0   
3     Los Angeles County    0.55  ...    0      0        0      0       0   
4     Los Angeles County    0.31  ...    0      0        0      0       0   
...                  ...     ...  ...  ...    ...      ...    ...     ...   
2337  Los Angeles County    0.19  ...    0      0        0      0       0   
2338  Los Angeles County    0.19  ...    0      0        0      0       0   
2339  Los Angeles County    0.13  ...    0      0        0      0       0   
2340  Los Angeles County    0.04  ...    0      0        0      0       1   
2341  Los Angeles County    0.99  ...    0      0        0      0       0   

      EAL_ET  EBL_ET  EB_ET  PM25_ET  \
0          0       0      0        0   
1          0       0      0        0   
2          0       0      0        0   
3          0       0      0        0   
4          0       0      0        0   
...      ...     ...    ...      ...   
2337       0       0      0        1   
2338       0       0      0        1   
2339       0       0      0        1   
2340       0       0      0        0   
2341       0       0      0        1   

                                             geometry_y  
0     POLYGON ((-118.30089 34.25869, -118.30087 34.2...  
1     POLYGON ((-118.29825 34.27750, -118.29823 34.2...  
2     POLYGON ((-118.29792 34.25451, -118.29945 34.2...  
3     POLYGON ((-

In [13]:
"""
m = folium.Map(location=(df_lat,df_lon), zoom_start=10)

folium.GeoJson(
    df_justice,
).add_to(m)

popup = folium.GeoJsonPopup(
    fields=["Neighborhood",'DF_PFS','AF_PFS','HDF_PFS'],
    aliases=["Neighborhood:", "% Adults with Diabetes:", 
             "% Adults with Asthma:", "% Adults with Coronary Artery Disease"],
    localize=True,
    sticky=False,
    labels=True,
    style=
        "background-color: #F0EFEF;border: 2px solid black;border-radius: 3px;box-shadow: 3px;",
    max_width=800,
)


folium.Choropleth(
    geo_data=df_justice,
    data=df_justice,
    key_on="feature.properties.GEOID10",
    columns=['GEOID10','HBF_PFS'],
    fill_color='YlGnBu',
    fill_opacity=0.5,
    popup = popup,
).add_to(m)

m
"""

'\nm = folium.Map(location=(df_lat,df_lon), zoom_start=10)\n\nfolium.GeoJson(\n    df_justice,\n).add_to(m)\n\npopup = folium.GeoJsonPopup(\n    fields=["Neighborhood",\'DF_PFS\',\'AF_PFS\',\'HDF_PFS\'],\n    aliases=["Neighborhood:", "% Adults with Diabetes:", \n             "% Adults with Asthma:", "% Adults with Coronary Artery Disease"],\n    localize=True,\n    sticky=False,\n    labels=True,\n    style=\n        "background-color: #F0EFEF;border: 2px solid black;border-radius: 3px;box-shadow: 3px;",\n    max_width=800,\n)\n\n\nfolium.Choropleth(\n    geo_data=df_justice,\n    data=df_justice,\n    key_on="feature.properties.GEOID10",\n    columns=[\'GEOID10\',\'HBF_PFS\'],\n    fill_color=\'YlGnBu\',\n    fill_opacity=0.5,\n    popup = popup,\n).add_to(m)\n\nm\n'

In [14]:
df_justice_neigh_subset = df_just_neigh[500:1000]
df_justice_neigh_subset = gpd.GeoDataFrame(df_justice_neigh_subset,geometry='geometry_y')

In [15]:
df_justice_neigh_subset = df_justice_neigh_subset.drop(columns=['geometry_x'])

In [16]:
m_subset = folium.Map(location=(df_lat,df_lon), zoom_start=10)

folium.GeoJson(
    df_justice_neigh_subset,
).add_to(m_subset)

popup = folium.GeoJsonPopup(
    fields=["GEOID10",'DF_PFS','AF_PFS','HDF_PFS'],
    aliases=["Neighborhood:", "% Adults with Diabetes:", 
             "% Adults with Asthma:", "% Adults with Coronary Artery Disease"],
    localize=True,
    sticky=False,
    labels=True,
    style=
        "background-color: #F0EFEF;border: 2px solid black;border-radius: 3px;box-shadow: 3px;",
    max_width=800,
)


folium.Choropleth(
    geo_data=df_justice_neigh_subset,
    data=df_justice_neigh_subset,
    key_on="feature.properties.GEOID10",
    columns=['GEOID10','HBF_PFS'],
    fill_color='YlGnBu',
    fill_opacity=0.5,
    popup = popup
).add_to(m_subset)


In [17]:
m_subset